In [1]:
import pandas as pd
import matplotlib.pyplot as plt
import matplotlib.ticker as ticker
import matplotlib.patheffects as path_effects
import matplotlib.font_manager as fm
from matplotlib.patches import RegularPolygon
import matplotlib.patches as mpatches
from matplotlib.offsetbox import OffsetImage, AnnotationBbox
from matplotlib import cm
from matplotlib import colormaps
import numpy as np
from ast import literal_eval
import math
from highlight_text import fig_text, ax_text

from PIL import Image
from io import BytesIO
import urllib
import os
import glob
import os
from mplsoccer import add_image
from urllib.request import urlopen

In [2]:
red = '#cb2217'
blue = '#00285e'
sky_blue = '#6caddf'
bg_color= '#fffcf7'
gold = '#ffc758'

font_path = "../assets/fonts"
for x in os.listdir(font_path):
    for y in os.listdir(f"{font_path}/{x}"):
        if (y.split(".")[-1] == "ttf") or (y.split(".")[-1] == "otf"):
            fm.fontManager.addfont(f"{font_path}/{x}/{y}")
            try:
                fm.FontProperties(weight=y.split("-")[-1].split(".")[0].lower(), fname=y.split("-")[0])
            except Exception:
                continue
                
plt.style.use("soc_base.mplstyle")

In [10]:
# path = r'C:\Users\Hp2\Music\joel\Análisis de fulbo\WSL24-25' # use the path with your data
path = r'C:\Users\MIRIRAI\Documents\Joel\Analisis-de-fulbo-main\WSL24-25'
all_files = glob.glob(os.path.join(path, "*.csv"))
j = 1

df = pd.DataFrame()
for file in all_files:
    df_match = pd.read_csv(file)
    df_match["match_id"] = j
    df = pd.concat([df, df_match], ignore_index=True)
    j+=1


# df = pd.concat((pd.read_csv(f) for f in all_files), ignore_index=True)

In [11]:
df

level_0  index  eventId  minute  second  teamId       x       y  \
0             0      1      2.0     0.0     0.0   30998   0.000   0.000   
1             1      2      2.0     0.0     0.0   31010   0.000   0.000   
2             2      3    781.0     0.0     1.0   30998  52.290  34.068   
3             3      4    782.0     0.0     1.0   30998  37.275  39.576   
4             4      5    783.0     0.0     5.0   30998  28.245  25.704   
...         ...    ...      ...     ...     ...     ...     ...     ...   
237550     1824   1825  11893.0    86.0     NaN   31006  83.055  56.168   
237551     1825   1826    779.0     0.0     0.0   31000   0.000   0.000   
237552     1826   1827    979.0     0.0     0.0   31006   0.000   0.000   
237553     1827   1828      1.0     0.0     0.0   31000   0.000   0.000   
237554     1828   1829      1.0     0.0     0.0   31006   0.000   0.000   

        expandedMinute      period  ...               name position  \
0                  0.0   FirstHalf  ...                NaN      NaN   
1                  0.0   FirstHalf  ...                NaN      NaN   
2                  0.0   FirstHalf  ...      Alessia Russo       FW   
3                  0.0   FirstHalf  ...  Mariona Caldentey      DMC   
4                  0.0   FirstHalf  ...    Leah Williamson       DC   
...                ...         ...  ...                ...      ...   
237550            90.0  SecondHalf  ...        Hayley Raso      Sub   
237551            10.0    PostGame  ...                NaN      NaN   
237552            10.0    PostGame  ...                NaN      NaN   
237553             0.0    PreMatch  ...                NaN      NaN   
237554             0.0    PreMatch  ...                NaN      NaN   

       isFirstEleven  prog_pass  prog_carry  pass_or_carry_angle  \
0                NaN   0.000000         0.0                  NaN   
1                NaN   0.000000         0.0                  NaN   
2               True -15.126395         0.0           156.205777   
3               True  -9.247875         0.0          -123.062178   
4               True   1.924863         0.0            82.352572   
...              ...        ...         ...                  ...   
237550           NaN   0.000000         0.0                  NaN   
237551           NaN   0.000000         0.0                  NaN   
237552           NaN   0.000000         0.0                  NaN   
237553           NaN   0.000000         0.0                  NaN   
237554           NaN   0.000000         0.0                  NaN   

            shortName  possession_id        possession_team  match_id  
0                 NaN            1.0          Arsenal Women         1  
1                 NaN            1.0          Arsenal Women         1  
2            A. Russo            1.0          Arsenal Women         1  
3        M. Caldentey            1.0          Arsenal Women         1  
4       L. Williamson            1.0          Arsenal Women         1  
...               ...            ...                    ...       ...  
237550        H. Raso          116.0  West Ham United Women       132  
237551            NaN          116.0  West Ham United Women       132  
237552            NaN          116.0  West Ham United Women       132  
237553            NaN          116.0  West Ham United Women       132  
237554            NaN          116.0  West Ham United Women       132  

[237555 rows x 52 columns]

In [12]:
def calculate_speed_metrics(df):
    """
    Calculate Speed and Direct Speed for each team.
    
    Speed: The speed of ball movement during a possession sequence. 
    Direct Speed: The average speed of ball progression towards the opponent’s goal.
    
    Args:
        df (pd.DataFrame): Processed J League events DataFrame.
    
    Returns:
        pd.DataFrame: DataFrame with Speed and Direct Speed metrics.
    """

    # Fill missing values and replace None or NaN with "Complete"
    # df['pass.outcome.name'] = df['pass.outcome.name'].fillna("Complete").replace({None: "Complete"})

    df_events = df.copy()

    match_ids = df_events["match_id"].unique()

    chains_data = []

    for match_id in match_ids:
        df_match = df_events[df_events["match_id"] == match_id]
        
        df_match['Time'] = df_match['minute'] * 60 + df_match['second']
        df_match['Time_diff'] = df_match['Time'].diff()
        df_match['Time_diff'].fillna(0, inplace = True)
        df_match["Time_diff"] = df_match["Time_diff"].shift(-1)
        
        df_match['ordinate'] = np.sqrt(df_match['x']**2 + df['y']**2)
        df_match['distance'] = np.abs(df_match['ordinate'].diff())
        df_match['distance'].fillna(0, inplace = True)
        df_match["distance"] = df_match["distance"].shift(-1)
        
        chains = pd.DataFrame()
        for v in df_match.possession_id.unique():
            chain = df_match.loc[df_match["possession_id"] == v]
            chain['Sequence Time'] = chain['Time_diff'].sum()
            
            chain['Progress'] = chain.iloc[-1].x - chain.iloc[0].x
            
            chain['Length'] = chain['distance'].sum()
            
            
            chain['Speed'] = chain['Length'] / chain['Sequence Time']
            chain['Direct Speed'] = chain['Progress'] / chain['Sequence Time']
            
            
            if chain.shape[0] >= 4:  
                
                chains = pd.concat([chains, chain], ignore_index=True)
            
        chains_data.append(chains)
            
    chains_data = pd.concat(chains_data) 

    ch = chains_data.groupby(['match_id', 'possession_id', 'possession_team']).agg({
    'Speed': 'first',           # Take the first value of speed for each group
    'Direct Speed': 'first'     # Take the first value of direct_speed for each group
    }).reset_index()

    ch_pos = ch.loc[ch["Direct Speed"] >= 0]
    pass_counts = chains_data[chains_data['type'] == 'Pass'].groupby(['possession_id','possession_team', 'match_id'])['type'].count().reset_index()
    r = ch_pos.merge(pass_counts, on=['match_id', 'possession_id', 'possession_team'], how = 'left')
    r_filter = r[~np.isinf(r['Direct Speed'])]
    a = r_filter.groupby(['possession_team.name']).agg({
        'Direct Speed': 'mean',           # Take the first value of speed for each group
        'Speed': 'mean',
    }).reset_index()


    a.columns = ['Team', 'Direct Speed Upfield(m/s)', 'Speed']

    return a

In [ ]:
metrics = calculate_speed_metrics(df)

C:\Users\MIRIRAI\AppData\Local\Temp\ipykernel_19376\3180866276.py:27: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_match['Time'] = df_match['minute'] * 60 + df_match['second']
C:\Users\MIRIRAI\AppData\Local\Temp\ipykernel_19376\3180866276.py:28: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_match['Time_diff'] = df_match['Time'].diff()
C:\Users\MIRIRAI\AppData\Local\Temp\ipykernel_19376\3180866276.py:29: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assi

In [15]:
metrics

NameError: name 'metrics' is not defined